<a href="https://colab.research.google.com/github/toraaglobal/SREIT/blob/master/03_initial_modeling_zip.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
## Import packages
from fbprophet import Prophet
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import sqlite3
import pickle
import datetime as dt
from sklearn.metrics import mean_squared_error


%matplotlib inline


In [2]:
## OBTAIN


#Mount the gdrive
import os
from google.colab import drive
drive.mount('/content/drive')


#change directry to the gdrive

os.chdir('./drive/My Drive/Colab Notebooks/code')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [0]:
## create a database connection
conn = sqlite3.connect('uszipmodel.sqlite')
cur = conn.cursor()

cur.execute('''
CREATE TABLE IF NOT EXISTS models (zip TEXT NOT NULL UNIQUE, model BLOB, mse REAL )''')
conn.commit()

In [0]:
## Read data

single_family = pd.read_csv('single_family_prep.csv')
single_family.head()

Unnamed: 0  RegionID  RegionName     City State  \
0           0     60657       60657  Chicago    IL   
1           1     77494       77494     Katy    TX   
2           2     60614       60614  Chicago    IL   
3           3     77449       77449     Katy    TX   
4           4     79936       79936  El Paso    TX   

                              Metro      CountyName  SizeRank        Date  \
0          Chicago-Naperville-Elgin     Cook County         1  1996-04-01   
1  Houston-The Woodlands-Sugar Land   Harris County         2  1996-04-01   
2          Chicago-Naperville-Elgin     Cook County         3  1996-04-01   
3  Houston-The Woodlands-Sugar Land   Harris County         4  1996-04-01   
4                           El Paso  El Paso County         5  1996-04-01   

     Values  
0  337200.0  
1  210400.0  
2  502900.0  
3   95400.0  
4   77300.0

In [0]:
single_family = single_family.rename(index=str, columns={'RegionName': "Zipcode"})
single_family['Date'] = pd.to_datetime(single_family['Date'])
single_family.head()

Unnamed: 0  RegionID  Zipcode     City State  \
0           0     60657    60657  Chicago    IL   
1           1     77494    77494     Katy    TX   
2           2     60614    60614  Chicago    IL   
3           3     77449    77449     Katy    TX   
4           4     79936    79936  El Paso    TX   

                              Metro      CountyName  SizeRank       Date  \
0          Chicago-Naperville-Elgin     Cook County         1 1996-04-01   
1  Houston-The Woodlands-Sugar Land   Harris County         2 1996-04-01   
2          Chicago-Naperville-Elgin     Cook County         3 1996-04-01   
3  Houston-The Woodlands-Sugar Land   Harris County         4 1996-04-01   
4                           El Paso  El Paso County         5 1996-04-01   

     Values  
0  337200.0  
1  210400.0  
2  502900.0  
3   95400.0  
4   77300.0

In [0]:
print(single_family.shape)
single_family.info()

(4272756, 10)
<class 'pandas.core.frame.DataFrame'>
Index: 4272756 entries, 0 to 4272755
Data columns (total 10 columns):
Unnamed: 0    int64
RegionID      int64
Zipcode       int64
City          object
State         object
Metro         object
CountyName    object
SizeRank      int64
Date          datetime64[ns]
Values        float64
dtypes: datetime64[ns](1), float64(1), int64(4), object(4)
memory usage: 358.6+ MB


In [0]:
# unique zipcodes
len(single_family['Zipcode'].unique())

15481

In [0]:
## Data type convertion
single_family['Zipcode'] = single_family['Zipcode'].astype(str)
single_family['RegionID'] = single_family['RegionID'].astype(str)
## Description
single_family.describe()

Unnamed: 0      SizeRank        Values
count  4.272756e+06  4.272756e+06  4.092412e+06
mean   2.136378e+06  7.741000e+03  2.062664e+05
std    1.233439e+06  4.468980e+03  2.422257e+05
min    0.000000e+00  1.000000e+00  1.120000e+04
25%    1.068189e+06  3.871000e+03  9.620000e+04
50%    2.136378e+06  7.741000e+03  1.458000e+05
75%    3.204566e+06  1.161100e+04  2.353000e+05
max    4.272755e+06  1.548100e+04  1.933810e+07

In [0]:
## Categorical variable decription
single_family.describe(include=['O'])

RegionID  Zipcode      City    State                        Metro  \
count   4272756  4272756   4272756  4272756                      3898224   
unique    15481    15481      7929       51                          775   
top       53527    53527  New York       CA  New York-Newark-Jersey City   
freq        276      276     32292   339756                       213624   

                CountyName  
count              4272756  
unique                1329  
top     Los Angeles County  
freq                 72864

In [0]:
## Training set : 1997 - 2017
## Test set : 2018

train_df = single_family[(single_family.Date.dt.year > 1996) & (single_family.Date.dt.year <= 2017) ]

test_df = single_family[single_family.Date.dt.year == 2018]

print('Train : {}'.format(train_df.shape))
print('Test : {}'.format(test_df.shape))



Train : (3901212, 10)
Test : (185772, 10)


In [0]:
train_df.head()

Unnamed: 0 RegionID Zipcode     City State  \
139329      139329    60657   60657  Chicago    IL   
139330      139330    77494   77494     Katy    TX   
139331      139331    60614   60614  Chicago    IL   
139332      139332    77449   77449     Katy    TX   
139333      139333    79936   79936  El Paso    TX   

                                   Metro      CountyName  SizeRank       Date  \
139329          Chicago-Naperville-Elgin     Cook County         1 1997-01-01   
139330  Houston-The Woodlands-Sugar Land   Harris County         2 1997-01-01   
139331          Chicago-Naperville-Elgin     Cook County         3 1997-01-01   
139332  Houston-The Woodlands-Sugar Land   Harris County         4 1997-01-01   
139333                           El Paso  El Paso County         5 1997-01-01   

          Values  
139329  344900.0  
139330  197300.0  
139331  503200.0  
139332   96600.0  
139333   77800.0

In [0]:
train_df.tail()

Unnamed: 0 RegionID Zipcode                 City State  \
4040536     4040536     1338    1338             Buckland    MA   
4040537     4040537     3293    3293            Woodstock    NH   
4040538     4040538    40404   40404                Berea    KY   
4040539     4040539    81225   81225  Mount Crested Butte    CO   
4040540     4040540    89155   89155             Mesquite    NV   

                                Metro       CountyName  SizeRank       Date  \
4040536               Greenfield Town  Franklin County     15477 2017-12-01   
4040537             Claremont-Lebanon   Grafton County     15478 2017-12-01   
4040538                Richmond-Berea   Madison County     15479 2017-12-01   
4040539                           NaN  Gunnison County     15480 2017-12-01   
4040540  Las Vegas-Henderson-Paradise     Clark County     15481 2017-12-01   

           Values  
4040536  218700.0  
4040537  211600.0  
4040538  131000.0  
4040539  713200.0  
4040540  344400.0

In [0]:
test_df.head()

Unnamed: 0 RegionID Zipcode     City State  \
4040541     4040541    60657   60657  Chicago    IL   
4040542     4040542    77494   77494     Katy    TX   
4040543     4040543    60614   60614  Chicago    IL   
4040544     4040544    77449   77449     Katy    TX   
4040545     4040545    79936   79936  El Paso    TX   

                                    Metro      CountyName  SizeRank  \
4040541          Chicago-Naperville-Elgin     Cook County         1   
4040542  Houston-The Woodlands-Sugar Land   Harris County         2   
4040543          Chicago-Naperville-Elgin     Cook County         3   
4040544  Houston-The Woodlands-Sugar Land   Harris County         4   
4040545                           El Paso  El Paso County         5   

              Date     Values  
4040541 2018-01-01  1028300.0  
4040542 2018-01-01   322600.0  
4040543 2018-01-01  1309300.0  
4040544 2018-01-01   173500.0  
4040545 2018-01-01   120200.0

In [0]:
test_df.tail()

Unnamed: 0 RegionID Zipcode                 City State  \
4226308     4226308     1338    1338             Buckland    MA   
4226309     4226309     3293    3293            Woodstock    NH   
4226310     4226310    40404   40404                Berea    KY   
4226311     4226311    81225   81225  Mount Crested Butte    CO   
4226312     4226312    89155   89155             Mesquite    NV   

                                Metro       CountyName  SizeRank       Date  \
4226308               Greenfield Town  Franklin County     15477 2018-12-01   
4226309             Claremont-Lebanon   Grafton County     15478 2018-12-01   
4226310                Richmond-Berea   Madison County     15479 2018-12-01   
4226311                           NaN  Gunnison County     15480 2018-12-01   
4226312  Las Vegas-Henderson-Paradise     Clark County     15481 2018-12-01   

           Values  
4226308  226000.0  
4226309  230200.0  
4226310  141600.0  
4226311  771600.0  
4226312  372200.0

In [0]:
## rename column for prophet model

train_df = train_df.rename(index=str, columns={'Date':'ds', 'Values':'y'})
test_df = test_df.rename(index=str, columns={'Date':'ds', 'Values':'y'})
single_family = single_family.rename(index=str, columns={'Date':'ds', 'Values':'y'})

train_df.head()

Unnamed: 0 RegionID Zipcode     City State  \
139329      139329    60657   60657  Chicago    IL   
139330      139330    77494   77494     Katy    TX   
139331      139331    60614   60614  Chicago    IL   
139332      139332    77449   77449     Katy    TX   
139333      139333    79936   79936  El Paso    TX   

                                   Metro      CountyName  SizeRank         ds  \
139329          Chicago-Naperville-Elgin     Cook County         1 1997-01-01   
139330  Houston-The Woodlands-Sugar Land   Harris County         2 1997-01-01   
139331          Chicago-Naperville-Elgin     Cook County         3 1997-01-01   
139332  Houston-The Woodlands-Sugar Land   Harris County         4 1997-01-01   
139333                           El Paso  El Paso County         5 1997-01-01   

               y  
139329  344900.0  
139330  197300.0  
139331  503200.0  
139332   96600.0  
139333   77800.0

In [0]:
def run_zip_model(df, zipcode, df_test):
  # initialize the model
  model = Prophet(interval_width=0.95)
  #check if Zipmodel already in database
  cur.execute("SELECT mse from models where zip = ?",(zipcode,))
  try:
    data = cur.fetchone()[0]
    print("Model found in database")
  except:
    model.fit(df)
    
    #future_dates = df_test['ds']
    #print(future_dates.head())
    
    forecast = model.predict(df_test)
    #print(forecast.head())
    #actual
    y_actual = df_test['y']
    y_predict = forecast['yhat']
    #score
    score =  mean_squared_error(y_actual, y_predict)
    print(score)
    cur.execute('''INSERT INTO models (zip,model,mse)
    VALUES (?,?,?)''',(zipcode,pickle.dumps(model),score))
    
    conn.commit()
 
  
  
 
  

In [0]:
tem = train_df[train_df['Zipcode'] == '60657']
tem_test = test_df[test_df['Zipcode']== '60657']


run_zip_model(tem, '60657', tem_test)

Model found in database


In [0]:

zips = train_df['Zipcode'].unique()

zips = list(zips)

len(zips)


15481

In [0]:
len(test_df['Zipcode'].unique())
  

15481

In [0]:
import random

random.shuffle(zips)

In [0]:
count = 0
for zip in zips:
  train = train_df[train_df['Zipcode'] == zip]
  test = test_df[test_df['Zipcode']== zip]
  run_zip_model(train, zip, test)
  count+=1
  print("Counts: {}".format(count))
  conn.commit()

/usr/local/lib/python3.6/dist-packages/fbprophet/forecaster.py:880: FutureWarning: Series.nonzero() is deprecated and will be removed in a future version.Use Series.to_numpy().nonzero() instead
  min_dt = dt.iloc[dt.nonzero()[0]].min()
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.


321958618.4590933
Counts: 1


/usr/local/lib/python3.6/dist-packages/fbprophet/forecaster.py:880: FutureWarning: Series.nonzero() is deprecated and will be removed in a future version.Use Series.to_numpy().nonzero() instead
  min_dt = dt.iloc[dt.nonzero()[0]].min()
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.


15481656.440245943
Counts: 2
Model found in database
Counts: 3


/usr/local/lib/python3.6/dist-packages/fbprophet/forecaster.py:880: FutureWarning: Series.nonzero() is deprecated and will be removed in a future version.Use Series.to_numpy().nonzero() instead
  min_dt = dt.iloc[dt.nonzero()[0]].min()
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.


...

/usr/local/lib/python3.6/dist-packages/fbprophet/forecaster.py:880: FutureWarning: Series.nonzero() is deprecated and will be removed in a future version.Use Series.to_numpy().nonzero() instead
  min_dt = dt.iloc[dt.nonzero()[0]].min()
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.


2201140475.215745
Counts: 6244


/usr/local/lib/python3.6/dist-packages/fbprophet/forecaster.py:880: FutureWarning: Series.nonzero() is deprecated and will be removed in a future version.Use Series.to_numpy().nonzero() instead
  min_dt = dt.iloc[dt.nonzero()[0]].min()
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.


57388420.85220445
Counts: 6245


/usr/local/lib/python3.6/dist-packages/fbprophet/forecaster.py:880: FutureWarning: Series.nonzero() is deprecated and will be removed in a future version.Use Series.to_numpy().nonzero() instead
  min_dt = dt.iloc[dt.nonzero()[0]].min()
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.


In [4]:
cur.execute('SELECT COUNT(*) FROM models')
for data in cur:
  print(data)

(981,)
